In [3]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
  print("_THIS_",type(features))
  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits/5, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"]),
  }
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)




In [4]:
# Load training and eval data
mnist = tf.contrib.learn.datasets.load_dataset("mnist")
train_data = mnist.train.images  # Returns np.array
train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
eval_data = mnist.test.images  # Returns np.array
eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

# Create the Estimator
mnist_classifier = tf.estimator.Estimator(
  model_fn=cnn_model_fn, model_dir="./models/mnist_convnet_model_test1")

# Set up logging for predictions
# Log the values in the "Softmax" tensor with label "probabilities"
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(
  tensors=tensors_to_log, every_n_iter=50)

# Train the model
train_input_fn = tf.estimator.inputs.numpy_input_fn(
  x={"x": train_data},
  y=train_labels,
  batch_size=100,
  num_epochs=None,
  shuffle=True)

mnist_classifier.train(
  input_fn=train_input_fn,
  steps=20000,
  hooks=[logging_hook])

# Evaluate the model and print results
eval_input_fn = tf.estimator.inputs.numpy_input_fn(
  x={"x": eval_data},
  y=eval_labels,
  num_epochs=1,
  shuffle=False)
predictions=mnist_classifier.predict(input_fn=eval_input_fn)
eval_result=mnist_classifier.evaluate(input_fn=eval_input_fn)
print(eval_result)

Extracting MNIST-data/train-images-idx3-ubyte.gz
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_task_type': 'worker', '_is_chief': True, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f675a515f50>, '_save_checkpoints_steps': None, '_keep_checkpoint_every_n_hours': 10000, '_service': None, '_num_ps_replicas': 0, '_tf_random_seed': None, '_master': '', '_num_worker_replicas': 1, '_task_id': 0, '_log_step_count_steps': 100, '_model_dir': '/tmp/mnist_convnet_model_test1', '_save_summary_steps': 100}
_THIS_ <type 'dict'>
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model_test1/model.ckpt.
INFO:tensorflow:probabilities = [[0.10065992 0.09888237 0.1

INFO:tensorflow:loss = 2.3177974, step = 1
INFO:tensorflow:probabilities = [[0.09952555 0.09823677 0.09956051 0.0991494  0.10214091 0.10193001
  0.10043369 0.10124213 0.09899022 0.09879083]
 [0.10102481 0.09858397 0.10024894 0.09860893 0.1013011  0.10114671
  0.09945878 0.10085244 0.09845287 0.10032144]
 [0.10000785 0.09758276 0.09980252 0.09919203 0.1019633  0.10090586
  0.1006237  0.10009088 0.0987856  0.1010455 ]
 [0.0988283  0.10060095 0.10090865 0.09756039 0.10126417 0.1012312
  0.10124958 0.09941354 0.09909162 0.09985162]
 [0.10160027 0.0992289  0.09973212 0.09892066 0.1014269  0.10057461
  0.1001592  0.10053012 0.09915087 0.09867635]
 [0.09942304 0.09930499 0.09992806 0.09918922 0.10117442 0.10156818
  0.10029367 0.09913987 0.09840631 0.10157228]
 [0.09990605 0.09895278 0.09949629 0.10091955 0.10184985 0.09972297
  0.10003462 0.09957767 0.09961465 0.09992563]
 [0.09972157 0.10156719 0.10014518 0.09857652 0.10048693 0.10000078
  0.09997819 0.10006072 0.09842122 0.10104176]
 [0.09

INFO:tensorflow:global_step/sec: 54.2066
INFO:tensorflow:probabilities = [[0.10181122 0.0969669  0.1009138  0.09771971 0.10209411 0.10168914
  0.10008208 0.09882058 0.09876336 0.10113906]
 [0.10028614 0.09920531 0.10214275 0.0984128  0.10105352 0.09990191
  0.10029883 0.09881242 0.09902957 0.10085677]
 [0.10115824 0.09905444 0.10030893 0.09924171 0.10116459 0.09885049
  0.10009275 0.10129255 0.09918647 0.09964979]
 [0.10025648 0.09974483 0.10185076 0.09862066 0.10093611 0.10136998
  0.10141377 0.09913221 0.09808434 0.09859078]
 [0.10162588 0.09782761 0.09896393 0.09733823 0.09997576 0.10023148
  0.10126243 0.10184448 0.09929621 0.10163394]
 [0.1030485  0.09814045 0.09931665 0.09642267 0.10227367 0.1003723
  0.10082781 0.09988876 0.09897981 0.10072933]
 [0.09936229 0.10071845 0.0985537  0.10010033 0.10246642 0.10070451
  0.10131647 0.09852294 0.09717672 0.10107821]
 [0.10208272 0.09953516 0.09911177 0.09813458 0.10240044 0.10041639
  0.1025257  0.09917258 0.09841692 0.09820376]
 [0.1004

INFO:tensorflow:loss = 2.2951381, step = 101 (1.850 sec)
INFO:tensorflow:probabilities = [[0.10035668 0.09986516 0.10025995 0.09836446 0.10139871 0.10100133
  0.10150746 0.09794162 0.09817983 0.10112476]
 [0.09981305 0.09930256 0.10057653 0.09968102 0.10069151 0.09911969
  0.10013951 0.09997487 0.10007452 0.10062675]
 [0.09941685 0.09889698 0.10051127 0.09949459 0.09997739 0.1007166
  0.10080318 0.10224576 0.0980741  0.09986325]
 [0.10059486 0.10029276 0.10232762 0.10066798 0.09981447 0.10067231
  0.1004662  0.09711565 0.09767679 0.10037133]
 [0.10175613 0.09966262 0.09954964 0.10048845 0.1012607  0.09984865
  0.09957121 0.10112648 0.0978272  0.09890891]
 [0.09968984 0.09909167 0.10130984 0.10058627 0.10151157 0.09895641
  0.0999934  0.10005344 0.09807232 0.10073521]
 [0.09869307 0.10037261 0.10158534 0.09822342 0.09978034 0.09868453
  0.09916341 0.10239122 0.09849428 0.10261185]
 [0.1020282  0.10093945 0.10239331 0.09899764 0.09964592 0.09894571
  0.10137141 0.09757341 0.10002518 0.09

INFO:tensorflow:global_step/sec: 59.5411
INFO:tensorflow:probabilities = [[0.09959705 0.10029942 0.10122451 0.09815051 0.10105767 0.09952624
  0.10037832 0.09988787 0.0995357  0.10034271]
 [0.09793878 0.09829017 0.10011781 0.10071056 0.10203455 0.10050215
  0.10249677 0.10039674 0.09820635 0.09930621]
 [0.10145973 0.09890396 0.09833536 0.09865911 0.10209884 0.10152245
  0.09872781 0.10005391 0.09977928 0.10045955]
 [0.09850155 0.10178544 0.1005299  0.09864217 0.10227205 0.09897796
  0.10098935 0.1008186  0.09809455 0.09938845]
 [0.09971029 0.0998496  0.10077585 0.10021708 0.10099654 0.09989103
  0.10087483 0.09825309 0.09940966 0.10002209]
 [0.09941719 0.09862023 0.10017837 0.09762215 0.10146492 0.10190574
  0.10205885 0.10029808 0.09834243 0.10009202]
 [0.1001462  0.09961803 0.09958135 0.09930315 0.10181141 0.09907826
  0.0997733  0.10169996 0.09832299 0.10066541]
 [0.10044897 0.09748431 0.09982099 0.10111476 0.10090765 0.09961504
  0.10323513 0.09774084 0.10008916 0.0995432 ]
 [0.099

...

INFO:tensorflow:global_step/sec: 64.4122
INFO:tensorflow:probabilities = [[0.6270544  0.01307967 0.07222997 0.04858808 0.02132525 0.05714701
  0.04506269 0.02035314 0.03126859 0.06389122]
 [0.09242274 0.07987647 0.08055741 0.2152864  0.04005567 0.18792124
  0.06565386 0.04482135 0.11820081 0.07520402]
 [0.06010526 0.14799783 0.07023522 0.06995098 0.0768581  0.15558417
  0.239732   0.02450229 0.10501698 0.05001714]
 [0.04975002 0.05371857 0.08088516 0.11304799 0.0271244  0.07324962
  0.02963261 0.03212801 0.46869093 0.07177266]
 [0.033887   0.05692717 0.11553062 0.14491954 0.02275174 0.02457802
  0.00934133 0.44082877 0.04704003 0.10419582]
 [0.04886981 0.02715291 0.0284202  0.08592123 0.05447984 0.16858995
  0.03181384 0.04273681 0.37038508 0.14163035]
 [0.04044046 0.02144049 0.06179745 0.11161228 0.06298131 0.0837767
  0.02795596 0.02455117 0.44631347 0.11913067]
 [0.03842639 0.03954531 0.1527034  0.0486276  0.14215636 0.06770492
  0.3305562  0.04975213 0.07146962 0.05905809]
 [0.0513

INFO:tensorflow:loss = 0.19990289, step = 19801 (1.544 sec)
INFO:tensorflow:probabilities = [[0.04076292 0.02657629 0.03596241 0.0985924  0.08969113 0.4045971
  0.08743968 0.03925527 0.09922871 0.07789417]
 [0.03980391 0.03147928 0.08563902 0.09670371 0.0226751  0.03471579
  0.00798119 0.52244735 0.0455918  0.11296283]
 [0.05704532 0.03095378 0.04422158 0.11980018 0.02643735 0.48206195
  0.02462036 0.05917126 0.09963817 0.05605005]
 [0.13062212 0.02972379 0.16742133 0.12219097 0.04671184 0.0753566
  0.03725213 0.17155488 0.1257251  0.09344127]
 [0.05398589 0.07100144 0.06268205 0.17104734 0.03711008 0.29359287
  0.06137218 0.04897659 0.09523539 0.10499621]
 [0.05058444 0.00846465 0.06141865 0.01537614 0.5248708  0.0642633
  0.08736493 0.03634797 0.05019829 0.10111077]
 [0.04045646 0.01844853 0.53713614 0.12087116 0.00495193 0.01764187
  0.01609262 0.02056209 0.21598089 0.0078583 ]
 [0.06225658 0.0395495  0.09425066 0.08682558 0.03045325 0.03003274
  0.00824745 0.5457529  0.03532927 0.0

INFO:tensorflow:global_step/sec: 63.9706
INFO:tensorflow:probabilities = [[0.48898312 0.04830616 0.09787975 0.07882094 0.0239888  0.06685079
  0.07039784 0.04310178 0.02832661 0.05334418]
 [0.03914303 0.02865871 0.02870863 0.09036811 0.2304667  0.06387931
  0.02225566 0.11081588 0.08039167 0.30531222]
 [0.03873525 0.04136011 0.06850673 0.04439538 0.04677707 0.0664782
  0.0548054  0.03246364 0.56317973 0.04329855]
 [0.02401781 0.04866135 0.5113749  0.1302146  0.06504899 0.07139573
  0.02630125 0.04228264 0.04593703 0.03476567]
 [0.03816436 0.05522006 0.5924245  0.10266145 0.00757736 0.02957471
  0.01330904 0.0117616  0.13770176 0.01160513]
 [0.02732649 0.05350188 0.05749608 0.07661574 0.24815665 0.06441211
  0.04952251 0.15060306 0.04133166 0.23103377]
 [0.06469962 0.03399104 0.09811057 0.3729759  0.03460362 0.11117176
  0.02998317 0.02947561 0.12734619 0.09764256]
 [0.77155113 0.00731562 0.04164936 0.01270133 0.0077186  0.03438703
  0.0791307  0.0086046  0.02167441 0.0152672 ]
 [0.0311

INFO:tensorflow:loss = 0.07428821, step = 19901 (1.569 sec)
INFO:tensorflow:probabilities = [[0.08946782 0.03059031 0.02435576 0.11959923 0.06297022 0.38549352
  0.0448858  0.04743147 0.09849344 0.09671242]
 [0.0229084  0.06835169 0.07309855 0.15502101 0.0915056  0.02066422
  0.01647848 0.3205327  0.08844849 0.14299084]
 [0.07456209 0.05425645 0.10446061 0.21349527 0.02693701 0.06981606
  0.0476804  0.03527343 0.3054142  0.06810445]
 [0.07611588 0.03634705 0.1150319  0.03876215 0.09114004 0.10709038
  0.4391458  0.02039749 0.04877147 0.02719785]
 [0.04477029 0.02412879 0.6331553  0.08979497 0.02092387 0.02771445
  0.04940581 0.00990635 0.07118259 0.02901756]
 [0.06936176 0.079716   0.34743086 0.18050903 0.01934545 0.03050175
  0.01857606 0.06933276 0.13134475 0.05388155]
 [0.07713859 0.2724704  0.06462331 0.05672632 0.04458163 0.11926544
  0.08704086 0.07646833 0.15677077 0.04491432]
 [0.12525064 0.03200381 0.11742145 0.15530172 0.06446513 0.07917147
  0.07438721 0.02785958 0.23146096 

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model_test1/model.ckpt.
INFO:tensorflow:Loss for final step: 0.09934888.
_THIS_ <type 'dict'>
INFO:tensorflow:Starting evaluation at 2018-05-06-10:01:15
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model_test1/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-05-06-10:01:16
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9687, global_step = 20000, loss = 0.10273908
{'loss': 0.10273908, 'global_step': 20000, 'accuracy': 0.9687}
